ASSIGNMENT 1: SPARK

# Kaggle: Spooky Author Identification
Developed to run in Databricks environment

- https://www.kaggle.com/competitions/spooky-author-identification

Competition Task: Predict the author of excerpts from horror stories by Edgar Allan Poe, Mary Shelley, and HP Lovecraft.

Competition Files:
- train.csv (training dataset 3.14 MB)
- test.csv (test dataset 1.28 MB)

Data Fields:
- The training dataset has 3 fields:
  - id (String): unique identifier
  - text (String): text excerpt by one of the named authors
  - author (String): author of the given text excerpt (EAP, MWS, HPL)

## 1. Project Setup

1.1 Inspect Spooky Files

Preview train.csv and test.csv before loading and defining schemas

The train.csv file reveals 3 columns:
- id
- text
- author

In [ ]:
spark.read.csv("../sample-data/train.csv", header=True, inferSchema=True)

While test.csv file has only 2 columns:

- id
- text



In [0]:

%fs head /FileStore/tables/test.csv

1.2 Project Imports

In [0]:
from pyspark.sql.types import StructType, StructField, StringType # Schema definition
from pyspark.sql.functions import col, length, avg, stddev, min, max, explode, split, lower, trim
from pyspark.ml.feature import Tokenizer, RegexTokenizer, StopWordsRemover, CountVectorizer, IDF, StringIndexer
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier, NaiveBayes
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.functions import vector_to_array

1.3 Define Schemas

We could use Sparks infer schema here, but it's best practice to manually define the schema.

In [0]:
# Train.csv
trainSchema = StructType([
    StructField("id", StringType(), True),
    StructField("text", StringType(), True),
    StructField("author", StringType(), True)
])

# Test.csv (no author)
testSchema = StructType([
    StructField("id", StringType(), True),
    StructField("text", StringType(), True)
])

1.4 Create Dataframes

Load & Show Data

In [0]:

# File paths (kaggle files uploaded to Databrickss)
trainPath = "/FileStore/tables/train.csv"
testPath = "/FileStore/tables/test.csv"
# File type being read
fileType = "csv"
# Load kaggle train.csv into Dataframe
k_trainDF = (
    spark.read.format(fileType)
        .option('header', 'true')
        .option('escape', '"') # ensures csv is read by spark correctly
        .option('quote', '"')
        .option('multiLine', 'true')
        .schema(trainSchema)
        .load(trainPath)
)

# Load kaggle test.csv into Dataframe
k_testDF = (
    spark.read.format(fileType)
        .option('header', 'true')
        .option('escape', '"')
        .schema(testSchema)
        .load(testPath)
)

# Quick check Dataframes before caching
k_trainDF.show(5, truncate=70) # show max 70 chars per field
k_testDF.show(5, truncate=70)

k_trainDF.printSchema()
k_testDF.printSchema()

+-------+----------------------------------------------------------------------+------+
|     id|                                                                  text|author|
+-------+----------------------------------------------------------------------+------+
|id26305|This process, however, afforded me no means of ascertaining the dim...|   EAP|
|id17569|It never once occurred to me that the fumbling might be a mere mist...|   HPL|
|id11008|In his left hand was a gold snuff box, from which, as he capered do...|   EAP|
|id27763|How lovely is spring As we looked from Windsor Terrace on the sixte...|   MWS|
|id12958|Finding nothing else, not even gold, the Superintendent abandoned h...|   HPL|
+-------+----------------------------------------------------------------------+------+
only showing top 5 rows

+-------+----------------------------------------------------------------------+
|     id|                                                                  text|
+-------+------------

1.5 Verify Data Integrity

Basic integrity check before deeper data analysis and normalisation

In [0]:

# check for null or empty values
trainNullCheck = k_trainDF.filter(
    (col("text").isNull()) | (col("text") == "") | (col("author").isNull())
)
testNullCheck = k_testDF.filter(
    (col("text").isNull()) | (col("text") == "")
)

print("Null check train dataframe:", trainNullCheck.count())
print("Null check test dataframe:", testNullCheck.count())

# Check for duplicate rows in training dataset
dupeCheckDF = (
    k_trainDF
        .groupBy("text", "author")
        .count()
        .where(col("count") > 1)
)

print("Check for duplicate values: ")
dupeCheckDF.show()

# Row count
print("Train dataframe row count: ", k_trainDF.count())
print("Test dataframe row count: ", k_testDF.count())

# No null, empty or duplicate values were found

# Check partitioning allocated
print("Number of partitions in Kaggle trainDF:", k_trainDF.rdd.getNumPartitions())
print("Number of partitions in Kaggle testDF:", k_testDF.rdd.getNumPartitions())

""" 
Sparks partitioning system usually automatically splits data into 8 partitions.
In this case, it hasn't as the train dataset is only 3.14 MB (extremely small for Spark!). 
I have forcibly repartitioned the train dataframe into 8 partitions.
However, for such a small dataset this won't provide any extra performance benefits and is just for demonstration purposes.
"""
k_trainDF = k_trainDF.repartition(8)
print("Number of partitions in Kaggle trainDF:", k_trainDF.rdd.getNumPartitions())

Null check train dataframe: 0
Null check test dataframe: 0
Check for duplicate values: 
+----+------+-----+
|text|author|count|
+----+------+-----+
+----+------+-----+

Train dataframe row count:  19579
Test dataframe row count:  8392
Number of partitions in Kaggle trainDF: 1
Number of partitions in Kaggle testDF: 1
Number of partitions in Kaggle trainDF: 8


1.6 Caching

Cache the training dataframe as it will undergo multiple transformations

In [0]:

k_trainDF.cache()
print("k_trainDF dataframe has been cached!")

k_trainDF dataframe has been cached!


## 2. Data Exploration

2.1 Author Exploration

In [0]:

print("====== Distinct Authors ======")
k_trainDF.select("author").distinct().show()

print("====== Distribution of Entries by Author ======")
authorDistributionDF = (
    k_trainDF
        .groupBy("author")
        .count()
        .orderBy(col("count").desc())
)
authorDistributionDF.show()

====== Distinct Authors ======
+------+
|author|
+------+
|   MWS|
|   HPL|
|   EAP|
+------+

====== Distribution of Entries by Author ======
+------+-----+
|author|count|
+------+-----+
|   EAP| 7900|
|   MWS| 6044|
|   HPL| 5635|
+------+-----+



2.2 Text Exploration

In [0]:
# Create copy of dataframe 'with column' textLen
textExplorationDF = (
    k_trainDF
        .withColumn("textLen", length(col("text")))
        .select("id", "author", "text", "textLen")
)

print("====== Longest Excerpts -> descending ======")
textExplorationDF.orderBy(col("textLen").desc()).show(100)

print("====== Shortest Excerpts -> ascending ======")
textExplorationDF.orderBy(col("textLen").asc()).show(10)

print("====== TextLen Column Stats ======")
textExplorationDF.select("textLen").describe().show()

"""
Findings:
- 19,579 text excerpts
- Longest text excerpt is 4,663 characters
- Shortest text excerpt is 21 characters
- Average text excerpt length is approx 149 characters
- Standard deviation in lenghth is appox 107 characters 
- The top 5 longest excerpts all belong to Mary Shelley (MWS)
- The very long text excerpts appear to be outliers, 
  the majority of entries are below 1000 characters
"""

====== Longest Excerpts -> descending ======
+-------+------+--------------------+-------+
|     id|author|                text|textLen|
+-------+------+--------------------+-------+
|id27184|   MWS|Diotima approache...|   4663|
|id17485|   MWS|Oh no I will beco...|   3048|
|id13677|   MWS|They are gone for...|   2275|
|id20439|   MWS|To chambers of pa...|   2200|
|id20549|   MWS|As for those who ...|   1849|
|id12818|   EAP|Burning with the ...|   1533|
|id20687|   EAP|I have much to sa...|   1523|
|id24207|   MWS|At first indeed t...|   1032|
|id19267|   MWS|This also was my ...|    995|
|id03319|   MWS|I invited him to ...|    993|
|id02143|   MWS|Oh God help me Le...|    983|
|id23272|   EAP|awful calamity wa...|    964|
|id06581|   MWS|They were certain...|    948|
|id05745|   MWS|It was in Rome th...|    924|
|id25287|   EAP|It should be reme...|    910|
|id04831|   EAP|To muse for long ...|    908|
|id14957|   HPL|A weak, filtered ...|    900|
|id24339|   MWS|He seemed incapab..

2.3 Text Length Distribution by Author

In [0]:
authorStatsDF = (
    textExplorationDF
        .groupBy("author")
        .agg(
            avg("textLen").alias("avgTxtLen"),
            stddev("textLen").alias("stdTxtLen"),
            min("textLen").alias("minTxtLen"),
            max("textLen").alias("maxTxtLen"))
        .orderBy(col("avgTxtLen").desc())
)

print("====== Distribution of Text Length by Author ======")
authorStatsDF.show()

"""
Findings:
- Average text length approximately the same across authors, ranging from 142 to 156 
  characters
- Standard deviation is considerably higher for MWS (127) - EAP (106), HPL (82)
- Min text Length is the same for all authors
"""

====== Distribution of Text Length by Author ======
+------+------------------+------------------+---------+---------+
|author|         avgTxtLen|         stdTxtLen|minTxtLen|maxTxtLen|
+------+------------------+------------------+---------+---------+
|   HPL|155.84347826086957| 82.02064723110335|       21|      900|
|   MWS|151.65982792852415|126.30500751783727|       21|     4663|
|   EAP|142.22594936708862|105.75133420774067|       21|     1533|
+------+------------------+------------------+---------+---------+

Out[8]: '\nFindings:\n- Average text length approximately the same across authors, ranging from 142 to 156 \n  characters\n- Standard deviation is considerably higher for MWS (127) - EAP (106), HPL (82)\n- Min text Length is the same for all authors\n'

2.4 Word Frequency

In [0]:
wordsDF =(
    textExplorationDF
    # explode text excerpts into single words
    .select("author", explode(split(col("text"), " ")).alias("rawWord"))
    # Convert to lowercase, trim whitespace
    .select("author", lower(trim(col("rawWord"))).alias("word"))
    # Ignore empty strings
    .filter(col("word")!="")
)

topWordsDF = (
    wordsDF
        .groupBy("word")
        .count()
        .orderBy(col("count").desc())
)
print("====== Top 20 Most Common Words ======")
topWordsDF.show(20)

topWordsByAuthorDF =(
    wordsDF
        .groupBy("author", "word")
        .count()
        .orderBy(col("count").desc())
)
print("====== Top 40 Most Common Words by Author ======")
topWordsByAuthorDF.show(40)

====== Top 20 Most Common Words ======
+-----+-----+
| word|count|
+-----+-----+
|  the|35425|
|   of|20931|
|  and|17507|
|   to|12778|
|    a|10672|
|    i|10383|
|   in| 9383|
|  was| 6471|
| that| 6142|
|   my| 5367|
|  had| 4369|
| with| 4334|
|   he| 4286|
|   it| 4129|
|  his| 4073|
|   as| 3802|
|  for| 3437|
|   at| 3207|
|which| 3206|
|  but| 3144|
+-----+-----+
only showing top 20 rows

====== Top 40 Most Common Words by Author ======
+------+----+-----+
|author|word|count|
+------+----+-----+
|   EAP| the|14887|
|   HPL| the|10923|
|   MWS| the| 9615|
|   EAP|  of| 8961|
|   MWS|  of| 6134|
|   HPL| and| 6090|
|   MWS| and| 6002|
|   HPL|  of| 5836|
|   EAP| and| 5415|
|   MWS|  to| 4812|
|   EAP|  to| 4722|
|   EAP|   a| 4674|
|   MWS|   i| 4155|
|   EAP|  in| 4086|
|   EAP|   i| 3599|
|   HPL|   a| 3293|
|   HPL|  to| 3244|
|   HPL|  in| 2713|
|   MWS|   a| 2705|
|   MWS|  my| 2632|
|   HPL|   i| 2629|
|   MWS|  in| 2584|
|   MWS| was| 2211|
|   EAP|that| 2139|
|   EAP| w

Top Words
- Overall 20 top words

In [0]:
display(topWordsDF.limit(100))

word count the 35425 of 20931 and 17507 to 12778 a 10672 i 10383 in 9383 was 6471 that 6142 my 5367 had 4369 with 4334 he 4286 it 4129 his 4073 as 3802 for 3437 at 3207 which 3206 but 3144 not 3097 from 2864 by 2815 is 2561 on 2440 this 2398 be 2287 were 2133 have 2102 her 2034 me 2018 all 1813 we 1721 or 1688 an 1682 you 1608 no 1605 one 1497 so 1472 when 1422 they 1403 upon 1391 been 1373 could 1288 its 1269 she 1243 would 1218 there 1208 their 1160 more 1109 some 1054 him 1036 what 1022 our 1002 now 980 into 960 are 938 than 930 very 915 if 879 will 850 who 849 only 839 these 736 about 731 up 717 any 716 even 685 your 670 did 661 yet 656 then 655 out 632 before 616 might 605 after 603 like 590 most 586 old 585 them 585 must 577 through 573 over 559 first 555 should 545 never 545 such 539 seemed 532 every 529 made 529 those 516 time 512 man 508 found 498 has 490 little 489 while 488 other 485 great 482 where 480

Databricks visualization. Run in Databricks to view.

## 3. Data Preparation & Feature Engineering
- Demonstration of a basic pipeline
- Sequential creation and testing of each feature
- Logistic Regression is manually implemented as final modelling step for testing    
  purposes

3.1 Split Training Dataset

Train/Validate Split 70/30


In [0]:
trainDF, valDF = k_trainDF.randomSplit([0.7, 0.3], seed=42)
trainDF.cache()
valDF.cache()

print("====== k_trainDF Split ======")
print("The original kaggle dataframe:", k_trainDF.count(), "rows")
print("trainDF:", trainDF.count(), "rows -", trainDF.count()/k_trainDF.count(), "%")
print("testDF:", valDF.count(), "rows -", valDF.count()/k_trainDF.count(), "%")

#  Transformations are done on a copy of trainDF to keep original in tact for final pipeline implementation
demoDF = trainDF.select("*")

====== k_trainDF Split ======
The original kaggle dataframe: 19579 rows
trainDF: 13830 rows - 0.7063690689003524 %
testDF: 5749 rows - 0.2936309310996476 %


3.2 Tokenization
- Plain tokenizer: splits strings on whitespace and returns array of tokens 
- Punctuation is preserveed

In [0]:
# Plain tokenizer - punctuation is preserved
tokenizer = Tokenizer(inputCol="text", outputCol="plainTokens")
tokenizedDF = tokenizer.transform(demoDF)

print("====== Plain Tokenizer Output ======")
tokenizedDF.select("author", "text", "plainTokens").show(10, truncate=50)

====== Plain Tokenizer Output ======
+------+--------------------------------------------------+--------------------------------------------------+
|author|                                              text|                                       plainTokens|
+------+--------------------------------------------------+--------------------------------------------------+
|   EAP|His warehouse was the resort of all the princip...|[his, warehouse, was, the, resort, of, all, the...|
|   HPL|The moribund hermit's rage and fear, swelling t...|[the, moribund, hermit's, rage, and, fear,, swe...|
|   MWS|Raymond was weak and exhausted, yet the interes...|[raymond, was, weak, and, exhausted,, yet, the,...|
|   HPL|As the weeks passed, I observed with regret tha...|[as, the, weeks, passed,, i, observed, with, re...|
|   MWS|Death, cruel and relentless, had entered these ...|[death,, cruel, and, relentless,, had, entered,...|
|   HPL|An' the smell was awful, like what it is araoun...|[an', the, smell

3.3 Regex Tokenization
- I ended up using this instead of the plain tokenizer
- Custom regex pattern allows you to define how you want to split the data
- More precision and control

In [0]:

# Use custom regex pattern - punctuation is removed
regexTokenizer =(
    RegexTokenizer(
        inputCol="text",
        outputCol="tokens",
        pattern="[^\w']+"  # splits on anything that is not a word char or apostrophe
    )
)

regexTokenizedDF = regexTokenizer.transform(demoDF)
print("====== Regex Tokenizer Output ======")
regexTokenizedDF.select("author", "text", "tokens").show(10, truncate=50)
display(regexTokenizedDF)

====== Regex Tokenizer Output ======
+------+--------------------------------------------------+--------------------------------------------------+
|author|                                              text|                                            tokens|
+------+--------------------------------------------------+--------------------------------------------------+
|   EAP|His warehouse was the resort of all the princip...|[his, warehouse, was, the, resort, of, all, the...|
|   HPL|The moribund hermit's rage and fear, swelling t...|[the, moribund, hermit's, rage, and, fear, swel...|
|   MWS|Raymond was weak and exhausted, yet the interes...|[raymond, was, weak, and, exhausted, yet, the, ...|
|   HPL|As the weeks passed, I observed with regret tha...|[as, the, weeks, passed, i, observed, with, reg...|
|   MWS|Death, cruel and relentless, had entered these ...|[death, cruel, and, relentless, had, entered, t...|
|   HPL|An' the smell was awful, like what it is araoun...|[an', the, smell

id text author tokens id00034 His warehouse was the resort of all the principal people of the place, and especially of the editorial corps a body which inspires all about it with profound veneration and awe. EAP List(his, warehouse, was, the, resort, of, all, the, principal, people, of, the, place, and, especially, of, the, editorial, corps, a, body, which, inspires, all, about, it, with, profound, veneration, and, awe) id00049 The moribund hermit's rage and fear, swelling to grotesque proportions, seemed likely to shatter what remained of his failing physique; and once a spasm caused him to clap his hands to his eyes and rush into the bathroom. HPL List(the, moribund, hermit's, rage, and, fear, swelling, to, grotesque, proportions, seemed, likely, to, shatter, what, remained, of, his, failing, physique, and, once, a, spasm, caused, him, to, clap, his, hands, to, his, eyes, and, rush, into, the, bathroom) id00079 Raymond was weak and exhausted, yet the interest he perceived to be excited on his account, filled him with proud pleasure. MWS List(raymond, was, weak, and, exhausted, yet, the, interest, he, perceived, to, be, excited, on, his, account, filled, him, with, proud, pleasure) id00107 As the weeks passed, I observed with regret that my new friend was indeed slowly but unmistakably losing ground physically, as Mrs. Herrero had suggested. HPL List(as, the, weeks, passed, i, observed, with, regret, that, my, new, friend, was, indeed, slowly, but, unmistakably, losing, ground, physically, as, mrs, herrero, had, suggested) id00108 Death, cruel and relentless, had entered these beloved walls. MWS List(death, cruel, and, relentless, had, entered, these, beloved, walls) id00128 An' the smell was awful, like what it is araound Wizard Whateley's ol' haouse. . . HPL List(an', the, smell, was, awful, like, what, it, is, araound, wizard, whateley's, ol', haouse) id00159 Where if anywhere had he been on those nights of daemoniac alienage? HPL List(where, if, anywhere, had, he, been, on, those, nights, of, daemoniac, alienage) id00161 These responses from aesthetes told a disturbing tale. HPL List(these, responses, from, aesthetes, told, a, disturbing, tale) id00198 I do not believe I need to wait for the full change as most have waited. HPL List(i, do, not, believe, i, need, to, wait, for, the, full, change, as, most, have, waited) id00239 The author who was much thought of in his day was one Miller, or Mill; and we find it recorded of him, as a point of some importance, that he had a mill horse called Bentham. EAP List(the, author, who, was, much, thought, of, in, his, day, was, one, miller, or, mill, and, we, find, it, recorded, of, him, as, a, point, of, some, importance, that, he, had, a, mill, horse, called, bentham) id00260 "My travels were long and the sufferings I endured intense. MWS List(my, travels, were, long, and, the, sufferings, i, endured, intense) id00276 And toward the shore on the opposite bank of the river I saw the white belfry surmounting what I took to be the Marsh refinery. HPL List(and, toward, the, shore, on, the, opposite, bank, of, the, river, i, saw, the, white, belfry, surmounting, what, i, took, to, be, the, marsh, refinery) id00292 Will you accompany me? MWS List(will, you, accompany, me) id00314 The newcomer was a thin, dark man of medium height attired in the clerical garb of the Anglican church. HPL List(the, newcomer, was, a, thin, dark, man, of, medium, height, attired, in, the, clerical, garb, of, the, anglican, church) id00400 We all sign the initials of the society after our names, in the fashion of the R. S. A., Royal Society of Arts the S. D. U. K., Society for the Diffusion of Useful Knowledge, c, c. EAP List(we, all, sign, the, initials, of, the, society, after, our, names, in, the, fashion, of, the, r, s, a, royal, society, of, arts, the, s, d, u, k, society, for, the, diffusion, of, useful, knowledge, c, c) id00408 We saw no need of the impulse for the propensity. EAP List(we, saw, no, nee

3.4 Stopword Remover
- Default list of english stopwords are removed (e.g. 'the, and, a, as...')
- Can create your own custom stopwords list by appending to the default

In [0]:

customStopWords = StopWordsRemover.loadDefaultStopWords("english") # to customise concat "+ ('word to remove', ...)"
print("====== Default & Custom Stop Words ======")
print(customStopWords)

remover = StopWordsRemover(inputCol="tokens", outputCol="filteredTokens", stopWords=customStopWords)
stopWordsRemovedDF = remover.transform(regexTokenizedDF)

print("====== Tokens Before/After Stopword Removal ======")
stopWordsRemovedDF.select("tokens", "filteredTokens").show(5, truncate=50)

====== Default & Custom Stop Words ======
['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', 'her', 'hers', 'herself', 'it', 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', '

3.5 Quick Exploration of Filtered Data
- Examined the data once more -- this time with the stopwords removed

In [0]:
# Top tokens
tokensDF = (
    stopWordsRemovedDF
        .select(explode(col("filteredTokens")).alias("token"))
        .groupBy("token")
        .count()
        .orderBy(col("count").desc())
)
print("====== Top 20 Filtered Words (tokens) ======")
tokensDF.show(20)

# Top tokens by authors
tokensByAuthorDF = (
    stopWordsRemovedDF
        .select("author", explode(col("filteredTokens")).alias("token"))
        .groupBy("author","token")
        .count()
        .orderBy(col("count").desc())
)
print("====== Top 20 Filtered Words (tokens) by Author ======")
tokensByAuthorDF.show(20)

# Top tokens HPL
tokensByHPL =(
    tokensByAuthorDF
        .filter(col("author") == "HPL")
        .orderBy(col("count").desc())
)
# tokensByHPL.show(50)

# Top tokens EAP
tokensByEAP =(
    tokensByAuthorDF
        .filter(col("author") == "EAP")
        .orderBy(col("count").desc())
)
# tokensByEAP.show(50)

# Top tokens MWS
tokensByMWS =(
    tokensByAuthorDF
        .filter(col("author") == "MWS")
        .orderBy(col("count").desc())
)
# tokensByMWS.show(50)

====== Top 20 Filtered Words (tokens) ======
+------+-----+
| token|count|
+------+-----+
|   one| 1078|
|  upon|  984|
|   yet|  512|
|  time|  507|
|   man|  491|
|  even|  485|
|  said|  477|
|  like|  440|
| might|  432|
|    us|  428|
|   old|  425|
|  must|  422|
| first|  421|
| night|  404|
| never|  404|
|  made|  390|
|seemed|  388|
|  life|  386|
|  eyes|  381|
|little|  379|
+------+-----+
only showing top 20 rows

====== Top 20 Filtered Words (tokens) by Author ======
+------+------+-----+
|author| token|count|
+------+------+-----+
|   EAP|  upon|  701|
|   EAP|   one|  427|
|   MWS|   one|  330|
|   HPL|   one|  321|
|   HPL|   old|  279|
|   EAP|  said|  233|
|   MWS|  life|  229|
|   MWS|   yet|  225|
|   EAP|little|  214|
|   MWS|    us|  198|
|   MWS|  love|  196|
|   HPL|seemed|  194|
|   EAP|   say|  193|
|   MWS| heart|  188|
|   HPL|  like|  185|
|   MWS|  eyes|  184|
|   EAP|  even|  183|
|   EAP| first|  182|
|   MWS| might|  181|
|   EAP|  time|  181|
+------+

HP Lovecraft (HPL) - Top 100 words

In [0]:

display(tokensByHPL.limit(100))

author token count HPL one 321 HPL old 279 HPL seemed 194 HPL like 185 HPL night 178 HPL man 169 HPL things 169 HPL time 165 HPL saw 165 HPL though 160 HPL came 153 HPL great 143 HPL men 140 HPL an' 138 HPL never 137 HPL thing 137 HPL house 135 HPL upon 133 HPL even 131 HPL found 131 HPL must 127 HPL heard 126 HPL whose 124 HPL yet 119 HPL many 117 HPL strange 117 HPL long 112 HPL might 112 HPL still 110 HPL place 108 HPL door 106 HPL two 105 HPL told 103 HPL beyond 103 HPL come 103 HPL street 102 HPL see 102 HPL knew 101 HPL much 101 HPL day 101 HPL room 99 HPL certain 97 HPL thought 97 HPL far 95 HPL first 94 HPL said 93 HPL light 92 HPL back 92 HPL last 92 HPL ancient 91 HPL life 91 HPL little 90 HPL seen 89 HPL made 88 HPL years 86 HPL new 86 HPL eyes 85 HPL felt 85 HPL know 85 HPL ever 84 HPL almost 83 HPL something 83 HPL black 83 HPL left 82 HPL well 81 HPL small 79 HPL away 79 HPL without 78 HPL since 77 HPL toward 77 HPL way 76 HPL dark 75 HPL city 74 HPL fear 73 HPL half 71 HPL stone 71 HPL began 71 HPL west 70 HPL every 70 HPL terrible 69 HPL sea 68 HPL around 67 HPL looked 67 HPL three 67 HPL face 66 HPL floor 66 HPL dreams 66 HPL mind 64 HPL another 64 HPL moon 64 HPL world 63 HPL horror 62 HPL o' 62 HPL dead 62 HPL people 62 HPL space 61 HPL white 61 HPL known 60 HPL alone 60 HPL nothing 59

Databricks visualization. Run in Databricks to view.

Edgar Allan Poe (EAP) - Top 100 words

In [0]:

display(tokensByEAP.limit(100))

author token count EAP upon 701 EAP one 427 EAP said 233 EAP little 214 EAP say 193 EAP even 183 EAP first 182 EAP time 181 EAP well 180 EAP however 176 EAP made 176 EAP us 174 EAP ' 170 EAP yet 168 EAP great 168 EAP thus 166 EAP much 165 EAP man 160 EAP two 154 EAP long 150 EAP found 147 EAP must 147 EAP every 143 EAP never 139 EAP might 139 EAP like 134 EAP still 134 EAP without 125 EAP whole 125 EAP length 124 EAP may 124 EAP day 123 EAP within 123 EAP head 122 EAP mr 121 EAP thought 119 EAP nothing 114 EAP eyes 112 EAP although 112 EAP many 110 EAP indeed 109 EAP way 108 EAP far 107 EAP seemed 104 EAP three 101 EAP night 101 EAP matter 99 EAP point 97 EAP good 94 EAP let 93 EAP old 93 EAP mind 93 EAP hand 92 EAP de 92 EAP make 91 EAP thing 90 EAP came 90 EAP left 89 EAP body 88 EAP see 87 EAP saw 86 EAP feet 86 EAP idea 84 EAP less 84 EAP course 84 EAP shall 84 EAP words 83 EAP means 82 EAP doubt 82 EAP room 82 EAP back 81 EAP seen 81 EAP light 80 EAP full 79 EAP door 79 EAP know 78 EAP manner 78 EAP fact 77 EAP took 75 EAP years 74 EAP moment 74 EAP general 73 EAP character 73 EAP place 73 EAP nearly 70 EAP voice 70 EAP right 70 EAP person 70 EAP nature 69 EAP whose 69 EAP altogether 69 EAP felt 69 EAP large 68 EAP immediately 68 EAP air 68 EAP end 67 EAP house 66 EAP death 66 EAP life 66 EAP became 66

Databricks visualization. Run in Databricks to view.

Mary Shelley (MWS) - Top 100 words

In [0]:

display(tokensByMWS.limit(100))

author token count MWS one 330 MWS life 229 MWS yet 225 MWS us 198 MWS love 196 MWS heart 188 MWS eyes 184 MWS might 181 MWS raymond 179 MWS even 171 MWS man 162 MWS time 161 MWS every 155 MWS said 151 MWS upon 150 MWS day 149 MWS must 148 MWS first 145 MWS death 142 MWS may 130 MWS never 128 MWS made 126 MWS shall 126 MWS night 125 MWS ever 122 MWS like 121 MWS father 120 MWS still 117 MWS mind 112 MWS perdita 107 MWS thought 106 MWS towards 106 MWS hope 105 MWS thus 103 MWS saw 101 MWS many 101 MWS last 100 MWS found 100 MWS nature 100 MWS felt 99 MWS whose 98 MWS long 97 MWS words 96 MWS came 94 MWS years 92 MWS became 92 MWS seemed 90 MWS fear 88 MWS voice 88 MWS friend 88 MWS adrian 86 MWS come 85 MWS soon 84 MWS earth 84 MWS spirit 83 MWS away 82 MWS see 80 MWS among 80 MWS tears 79 MWS world 79 MWS passed 78 MWS part 78 MWS soul 78 MWS hand 76 MWS let 75 MWS human 75 MWS little 75 MWS often 73 MWS heard 73 MWS return 73 MWS idris 72 MWS moment 72 MWS dear 72 MWS happiness 72 MWS sun 71 MWS well 71 MWS country 69 MWS alone 69 MWS far 68 MWS know 68 MWS misery 66 MWS lost 66 MWS gave 65 MWS feelings 65 MWS sea 65 MWS another 65 MWS light 64 MWS near 64 MWS good 64 MWS much 64 MWS england 63 MWS happy 63 MWS change 63 MWS place 63 MWS power 63 MWS feel 62 MWS men 61 MWS hands 60 MWS also 60 MWS become 59

Databricks visualization. Run in Databricks to view.

3.6 TF-IDF (Term Frequency - Inverse Documentation Frequency)
- A two step process involving CountVectorizer and IDF

Count vectorizer
- Convert filtered tokens into term frequency vectors

In [0]:

# Convert filtered tokens into term frequency vectors
countVec = CountVectorizer(inputCol="filteredTokens", outputCol="termFrequency")
countVec_model = countVec.fit(stopWordsRemovedDF)               # Fit countVec mode
vectorizedDF = countVec_model.transform(stopWordsRemovedDF)     # Tranform Dataframe

print("====== Term Frequency ======")
vectorizedDF.select("filteredTokens", "termFrequency").show(20, truncate=50)

====== Term Frequency ======
+--------------------------------------------------+--------------------------------------------------+
|                                    filteredTokens|                                     termFrequency|
+--------------------------------------------------+--------------------------------------------------+
|[warehouse, resort, principal, people, place, e...|(22384,[52,130,185,422,1035,1897,2069,5599,6869...|
|[moribund, hermit's, rage, fear, swelling, grot...|(22384,[16,18,97,183,230,517,1191,1303,1863,224...|
|[raymond, weak, exhausted, yet, interest, perce...|(22384,[2,94,272,298,306,455,458,528,1165,2419,...|
|[weeks, passed, observed, regret, new, friend, ...|(22384,[68,89,99,122,279,385,707,863,922,1390,2...|
|[death, cruel, relentless, entered, beloved, wa...|(22384,[41,225,335,542,2660,4444],[1.0,1.0,1.0,...|
|[an', smell, awful, like, araound, wizard, what...|(22384,[7,144,1117,2459,2483,3950,5043,7842,896...|
|           [anywhere, nights, daem

IDF (Inverse Documentation Frequency)
- Upweight unique words
- Downweight common words

In [0]:

idf = IDF(inputCol="termFrequency", outputCol="tfidfFeatures")
idf_model = idf.fit(vectorizedDF) # fit idf_model
tfidfDF = idf_model.transform(vectorizedDF) # Transform dataframe

print("====== TF-IDF Features ======")
tfidfDF.select("termFrequency", "tfidfFeatures").show(20, truncate=50)

====== TF-IDF Features ======
+--------------------------------------------------+--------------------------------------------------+
|                                     termFrequency|                                     tfidfFeatures|
+--------------------------------------------------+--------------------------------------------------+
|(22384,[52,130,185,422,1035,1897,2069,5599,6869...|(22384,[52,130,185,422,1035,1897,2069,5599,6869...|
|(22384,[16,18,97,183,230,517,1191,1303,1863,224...|(22384,[16,18,97,183,230,517,1191,1303,1863,224...|
|(22384,[2,94,272,298,306,455,458,528,1165,2419,...|(22384,[2,94,272,298,306,455,458,528,1165,2419,...|
|(22384,[68,89,99,122,279,385,707,863,922,1390,2...|(22384,[68,89,99,122,279,385,707,863,922,1390,2...|
|(22384,[41,225,335,542,2660,4444],[1.0,1.0,1.0,...|(22384,[41,225,335,542,2660,4444],[3.9817081437...|
|(22384,[7,144,1117,2459,2483,3950,5043,7842,896...|(22384,[7,144,1117,2459,2483,3950,5043,7842,896...|
|  (22384,[2652,3080,6252,10675],[

3.7 String Indexer
- Assign numeric index values to each unique author
- Authors are labelled from 0 to 1, 0 being most frequent and 2 least

In [0]:

si = StringIndexer(inputCol="author", outputCol="authorIndex")
si_model = si.fit(tfidfDF) # fit string indexer model
indexedDF = si_model.transform(tfidfDF) # Transform dataframe

print("====== Author String Indexing ======")
indexedDF.select("author", "authorIndex").show(10)

print("====== Label Order ======")
print(si_model.labels)

"""
String Indexing Label Ordering: ['EAP', 'MWS', 'HPL']
EAP -> 0
MWS -> 1
HPL -> 2
"""

====== Author String Indexing ======
+------+-----------+
|author|authorIndex|
+------+-----------+
|   EAP|        0.0|
|   HPL|        2.0|
|   MWS|        1.0|
|   HPL|        2.0|
|   MWS|        1.0|
|   HPL|        2.0|
|   HPL|        2.0|
|   HPL|        2.0|
|   HPL|        2.0|
|   EAP|        0.0|
+------+-----------+
only showing top 10 rows

====== Label Order ======
['EAP', 'MWS', 'HPL']
Out[17]: "\nString Indexing Label Ordering: ['EAP', 'MWS', 'HPL']\nEAP -> 0\nMWS -> 1\nHPL -> 2\n"

3.8 Logistic Regression Manual
- Testing basic pipeline with with logistic regression

In [0]:

lr_demo = LogisticRegression(featuresCol="tfidfFeatures", labelCol="authorIndex", regParam=0.1)
lr_model_demo = lr_demo.fit(indexedDF)              # Fit logistic regression model
lr_preds_demo = lr_model_demo.transform(indexedDF)

print("====== Logistic Regression Predictions ======")
lr_preds_demo.select("id", "author", "authorIndex", "prediction", "probability").show()

====== Logistic Regression Predictions ======
+-------+------+-----------+----------+--------------------+
|     id|author|authorIndex|prediction|         probability|
+-------+------+-----------+----------+--------------------+
|id00034|   EAP|        0.0|       0.0|[0.96006240178304...|
|id00049|   HPL|        2.0|       2.0|[0.02736386616541...|
|id00079|   MWS|        1.0|       1.0|[0.06961296061569...|
|id00107|   HPL|        2.0|       2.0|[0.08191137265469...|
|id00108|   MWS|        1.0|       1.0|[0.18320025462655...|
|id00128|   HPL|        2.0|       2.0|[0.03193269043645...|
|id00159|   HPL|        2.0|       2.0|[0.06774607763422...|
|id00161|   HPL|        2.0|       2.0|[0.03396396634197...|
|id00198|   HPL|        2.0|       2.0|[0.24457367474160...|
|id00239|   EAP|        0.0|       0.0|[0.95532536550354...|
|id00260|   MWS|        1.0|       1.0|[0.10815025211117...|
|id00276|   HPL|        2.0|       2.0|[0.06904639982673...|
|id00292|   MWS|        1.0|       1.0|

## 4. Model Creation & Evaluation

4.1 Pipeline Builder Function and MCE Evaluator
- buildPipeline function takes a classifier as a parameter (LR, NB, RF), and applies it as the final pipeline   
  stage.
- MCE (MulticlassClassificationEvaluator) evaluates the model's performance on logLoss - was also used   
  to test accuracy.

In [0]:

# Combines previous steps to build the pipeline
def buildPipeline(classifier):
    return Pipeline(
        stages=[
            regexTokenizer,     # Cell 34
            remover,            # Cell 36
            countVec,           # Cell 40
            idf,                # Cell 42
            si,                 # Cell 44
            classifier
        ]
    )

# evaluate logLoss
mce = MulticlassClassificationEvaluator(
    labelCol="authorIndex",
    predictionCol="prediction",
    probabilityCol="probability",   # need for logLoss evaluation
    metricName="logLoss"            # also tested accuracy here
)

4.2 Model Tuning Function
- modelTuningFunction uses CrossValidator to test each parameter combination
- Returns the best model, predictions and log loss value


In [0]:

def modelTuning(trainData, testData, pipeline, paramgrid, evaluator=mce, folds=3, parallelism=5):
    crossVal = CrossValidator(
        estimator = pipeline,               # trained pipeline
        estimatorParamMaps = paramgrid,     # hyperparameter tuning values
        evaluator = evaluator,              # multiclass classification evaluator for log loss
        numFolds = folds,                   # number of subsets to split the training data
        parallelism =  parallelism          # number of param settings tested in parallel
    )
    crossVal_model = crossVal.fit(trainData)
    predictions = crossVal_model.transform(testData)
    logloss = evaluator.evaluate(predictions)

    return crossVal_model, predictions, logloss

4.3 Logistic Regression
- Applies logistic (sigmoid) function to weighted sum of TF-IDF features to calculate probability of each author

In [0]:

lr = LogisticRegression(featuresCol="tfidfFeatures", labelCol="authorIndex", family="multinomial")

lr_paramGrid = (
    ParamGridBuilder()
        .addGrid(lr.regParam,[0.08, 0.09])
        .addGrid(lr.elasticNetParam, [0.0])
        .addGrid(countVec.vocabSize,[11500, 12000])
        .build()
)

# Build and fine tune Logistic Regression pipeline
lr_pipeline = buildPipeline(lr) 
lr_model, lr_preds, lr_logloss = modelTuning(trainDF, valDF, lr_pipeline, lr_paramGrid)

# Best model parameters
lr_bestModel = lr_model.bestModel           # Extract best model
lr_best = lr_bestModel.stages[-1]           # LR last step in pipeline
lr_countVec_best = lr_bestModel.stages[2]   # CountVec 3rd step in pipeline


print("\n=================== LR Predictions ===================")
lr_preds.show(5)

print("\n=================== LR LogLoss ===================")
print("LogLoss on 30% split       :", lr_logloss)

print("\n=================== LR Best Model ===================")
print("Best regParam              :", lr_best.getRegParam())
print("Best elasticNetParam       :", lr_best.getElasticNetParam())
print("Best vocabSize             :", lr_countVec_best.getVocabSize())


=================== LR Predictions ===================
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|     id|                text|author|              tokens|      filteredTokens|       termFrequency|       tfidfFeatures|authorIndex|       rawPrediction|         probability|prediction|
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|id00070|Yet, even then, I...|   MWS|[yet, even, then,...|[yet, even, check...|(12000,[0,2,5,9,1...|(12000,[0,2,5,9,1...|        1.0|[-1.8000968476202...|[0.01105778700637...|       1.0|
|id00123|The writer spoke ...|   EAP|[the, writer, spo...|[writer, spoke, a...|(12000,[39,69,99,...|(12000,[39,69,99,...|        0.0|[3.39036782274577...|[0.98646584468935...|       0.0|
|id00133|

4.4 Naive Bayes
- Applies Bayes theorem under assumption all features are independent of each other
- Returns probabilistic outcomes for each author 

In [0]:

nb = NaiveBayes(featuresCol="tfidfFeatures", labelCol="authorIndex", modelType="multinomial")

# Define hyperparameters for NB classifier
nb_paramGrid = (
    ParamGridBuilder()
        .addGrid(nb.smoothing, [560, 570, 580])
        .addGrid(countVec.vocabSize, [22000, 22500])
        .build()
)

# Build and fine tune NB pipeline
nb_pipeline = buildPipeline(nb) 
nb_model, nb_preds, nb_logloss = modelTuning(trainDF, valDF, nb_pipeline, nb_paramGrid)

# Best model parameters
nb_bestModel = nb_model.bestModel           # Extract best model
nb_best = nb_bestModel.stages[-1]           # NB last step in pipeline
nb_countVec_best = nb_bestModel.stages[2]   # CountVec 3rd step in pipeline


print("\n=================== NB Predictions ===================")
print("LogLoss on 30% split       :", nb_logloss)
print("\n=================== NB Best Model ===================")
print("Best smoothing             :", nb_best.getSmoothing())
print("Best vocabSize             :", nb_countVec_best.getVocabSize())
print("\n=================== NB Predictions ===================")
nb_preds.show(5)


=================== NB Predictions ===================
LogLoss on 30% split       : 0.5912778480258282

=================== NB Best Model ===================
Best smoothing             : 570.0
Best vocabSize             : 22500

=================== NB Predictions ===================
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|     id|                text|author|              tokens|      filteredTokens|       termFrequency|       tfidfFeatures|authorIndex|       rawPrediction|         probability|prediction|
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|id00070|Yet, even then, I...|   MWS|[yet, even, then,...|[yet, even, check...|(22384,[0,2,5,9,1...|(22384,[0,2,5,9,1...|        1.0|[-723.54346479882...|

4.5 Random Forest
- Type of decision tree algorithm - trains multiple trees instead of one (reduces risk of overfitting)

In [0]:
rf = RandomForestClassifier(featuresCol="tfidfFeatures", labelCol="authorIndex")

rf_paramGrid = (
    ParamGridBuilder()
        .addGrid(rf.maxDepth, [10, 15])
        .addGrid(rf.numTrees, [60, 100])
        .addGrid(countVec.vocabSize, [2000, 4000])
        .build()
)

rf_pipeline = buildPipeline(rf) # Random Forest pipeline
rf_model, rf_preds, rf_logLoss = modelTuning(trainDF, valDF, rf_pipeline, rf_paramGrid) # Model fine tuning

rf_bestModel = rf_model.bestModel # RF best model
rf_best = rf_bestModel.stages[-1] # RF -> last step in pipeline stages
countVec_best = rf_bestModel.stages[2] # CountVec -> 3rd step in pipeline stages

print("====== RF Predictions ======")
rf_preds.show(5)

print("====== RF LogLoss ======")
print("LogLoss on 30% split       :", rf_logLoss)

print("====== RF Best Model ======")
print("Best numTrees              :", rf_best.getNumTrees)
print("Best maxDepth              :", rf_best.getMaxDepth())
print("Best vocabSize             :", countVec_best.getVocabSize())

====== RF Predictions ======
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|     id|                text|author|              tokens|      filteredTokens|       termFrequency|       tfidfFeatures|authorIndex|       rawPrediction|         probability|prediction|
+-------+--------------------+------+--------------------+--------------------+--------------------+--------------------+-----------+--------------------+--------------------+----------+
|id00070|Yet, even then, I...|   MWS|[yet, even, then,...|[yet, even, check...|(2000,[0,2,5,9,11...|(2000,[0,2,5,9,11...|        1.0|[36.5762993546024...|[0.36576299354602...|       0.0|
|id00123|The writer spoke ...|   EAP|[the, writer, spo...|[writer, spoke, a...|(2000,[40,70,98,1...|(2000,[40,70,98,1...|        0.0|[42.0379316519967...|[0.42037931651996...|       0.0|
|id00133|Found in a Bottle...|   EAP

## 5. Kaggle Submission

5.1 Final Pipeline - Retraining & Generating Predictions
- Logistic regression was the top performing classifier
- Hardcode LR and its best param values into the final pipeline
- Pipeline is retrained on the full kaggle training file  - k_trainDF
- k_testDF (the unlabelled test set) is transformed by the trained pipeline to generate probability predictions

In [0]:

# Final Logistic Regression implementation with best values
logisticRegression = LogisticRegression(
    featuresCol="tfidfFeatures", 
    labelCol="authorIndex",
    regParam=0.09,
    elasticNetParam=0.0
)

# Update final vocab size
countVec.setVocabSize(11500)

# Build final pipeline with tuned LR
pipeline = buildPipeline(logisticRegression)

# Train the model on the full train file
trainedPL = pipeline.fit(k_trainDF)

# Final predictions based on full test file
final_preds = trainedPL.transform(k_testDF)
final_preds.select("id", "text", "prediction", "probability").show(5)

+-------+--------------------+----------+--------------------+
|     id|                text|prediction|         probability|
+-------+--------------------+----------+--------------------+
|id02310|Still, as I urged...|       1.0|[0.13479444020730...|
|id24541|If a fire wanted ...|       0.0|[0.83705385665936...|
|id00134|And when they had...|       2.0|[0.22179307587592...|
|id27757|While I was think...|       2.0|[0.47027982913499...|
|id04081|I am not sure to ...|       0.0|[0.84319002900923...|
+-------+--------------------+----------+--------------------+
only showing top 5 rows



5.2 Create Kaggle Submission File
- Check label ordering matches Kaggles submission requirements
- Organise columns
- Create submission CSV file

In [0]:

# Label ordering - ensure authors are in correct order for competition submission
string_indexer = trainedPL.stages[4] # si (string indexer) at index 4 of pipeline
labelOrder = string_indexer.labels
print("Label Order:", labelOrder)

kaggleDF = (
    final_preds
        .withColumn("probArray", vector_to_array(col("probability")))
        .withColumn("EAP", col("probArray")[labelOrder.index("EAP")])
        .withColumn("MWS", col("probArray")[labelOrder.index("MWS")])
        .withColumn("HPL", col("probArray")[labelOrder.index("HPL")])
        .select("id", "EAP", "MWS", "HPL")
)

# Review final submission DF
kaggleDF.show(10, truncate=False)
display(kaggleDF)

# Uncomment to create submission file - coalesce repartitions (if necessary) before writing file
# kaggleDF.coalesce(1).write.csv("/FileStore/tables/spookySub.csv", header=True)

Label Order: ['EAP', 'MWS', 'HPL']
+-------+-------------------+---------------------+--------------------+
|id     |EAP                |MWS                  |HPL                 |
+-------+-------------------+---------------------+--------------------+
|id02310|0.1347944402073078 |0.8113291676238609   |0.05387639216883136 |
|id24541|0.8370538566593693 |0.023099708194767844 |0.1398464351458628  |
|id00134|0.22179307587592462|0.015052794829501033 |0.7631541292945744  |
|id27757|0.4702798291349928 |0.019735858358769672 |0.5099843125062377  |
|id04081|0.8431900290092367 |0.09246901786496164  |0.06434095312580175 |
|id27337|0.4325554062991552 |0.04040306750728614  |0.5270415261935586  |
|id24265|0.5852345200583124 |0.1229289615772901   |0.2918365183643974  |
|id25917|0.1906415278919855 |0.5468666302606607   |0.2624918418473538  |
|id04951|0.9779549044564125 |0.0017186458575208913|0.020326449686066474|
|id14549|0.6921052207483169 |0.1741563980094436   |0.13373838124223938 |
+-------+-------

id EAP MWS HPL id02310 0.1347944402073078 0.8113291676238609 0.05387639216883136 id24541 0.8370538566593693 0.023099708194767844 0.1398464351458628 id00134 0.22179307587592462 0.015052794829501033 0.7631541292945744 id27757 0.4702798291349928 0.019735858358769672 0.5099843125062377 id04081 0.8431900290092367 0.09246901786496164 0.06434095312580175 id27337 0.4325554062991552 0.04040306750728614 0.5270415261935586 id24265 0.5852345200583124 0.1229289615772901 0.2918365183643974 id25917 0.1906415278919855 0.5468666302606607 0.2624918418473538 id04951 0.9779549044564125 0.0017186458575208913 0.020326449686066474 id14549 0.6921052207483169 0.1741563980094436 0.13373838124223938 id22505 0.01697958729357086 0.9146307267116723 0.06838968599475688 id24002 8.57860243584809E-4 3.476501692344102E-4 0.9987944895871809 id18982 0.09413697040798785 0.24780192932846865 0.6580611002635435 id15181 0.01124604243627112 0.002489782202803383 0.9862641753609256 id21888 0.6688332550923016 0.23617377036966494 0.09499297453803332 id12035 0.14580799683785137 0.7802820471060178 0.07390995605613095 id17991 0.25869472672500726 0.5526372689863513 0.1886680042886414 id10707 0.9980824861741053 0.0010874845881512511 8.300292377432188E-4 id07101 0.17412890922876403 0.7202029156722236 0.1056681750990123 id00345 0.0694456715295483 0.00653984858142807 0.9240144798890237 id05912 0.7632310058233893 0.14492575020082776 0.09184324397578282 id13443 0.9607737292614096 0.02666930242166031 0.012556968316929951 id09248 0.3296446871369981 0.548670663081628 0.12168464978137379 id17542 0.45262960333132013 0.07971364349861632 0.46765675317006344 id06995 0.04763854108275994 0.9029396768008456 0.04942178211639438 id25159 0.7063577195300341 0.20933791986290126 0.08430436060706462 id25729 0.6643588885432865 0.050240168307572455 0.2854009431491409 id26949 0.6558606794373886 0.09990686537993335 0.244232455182678 id27191 0.11844662660200694 0.8183389048206836 0.06321446857730942 id07668 0.041964365000381344 0.9445938853276423 0.013441749671976248 id02230 0.15753618926046797 0.49884735278543413 0.34361645795409795 id15553 0.9835592517972676 0.00932113432043178 0.007119613882300743 id25688 0.01903931463600101 0.015485473694399204 0.9654752116695997 id17545 0.9792289367930114 0.01044559490021172 0.010325468306776999 id13929 0.8356343430138999 0.07325762843672327 0.09110802854937675 id12880 0.3829078667572137 0.4899753062818381 0.12711682696094836 id19282 0.5059075692187299 0.2808984536344763 0.21319397714679364 id14690 0.10558798908158276 0.8079392072894488 0.08647280362896854 id17975 0.014082508149341559 0.027353445363386943 0.9585640464872716 id08037 0.6005907630010228 0.358558237486502 0.040850999512475346 id15412 0.1609494877762687 0.7910171473573548 0.048033364866376424 id25032 0.46656558637108514 0.3651714138107999 0.1682629998181149 id27165 0.9877212204805542 0.005771463924661541 0.0065073155947842345 id03327 0.7162629932163983 0.1260996826638167 0.1576373241197851 id18515 0.6889473374709791 0.22626828039472244 0.0847843821342985 id21003 0.3412571706577235 0.5935431430768727 0.06519968626540375 id23855 0.07163779003943857 0.14042795321363874 0.7879342567469227 id20724 0.6805118277649757 0.15912315828758397 0.16036501394744043 id13303 0.45876638421138455 0.40964477723194226 0.13158883855667325 id16521 0.013748685362814352 0.6454046913874073 0.3408466232497784 id20775 0.9940468411271958 6.874782186199825E-4 0.005265680654184178 id13029 0.8775733532556927 0.07333868649649429 0.04908796024781303 id14660 0.6597875202675184 0.09350921356026452 0.24670326617221705 id11028 0.017095408854373113 0.9722286571596507 0.010675933985976055 id14180 0.8636957018584377 0.06954590698238251 0.06675839115917973 id25860 0.9843791347753091 0.001124882738382773 0.014495982486308 id11910 0.6432852209324708 0.24926425397883392 0.1074505250886952 id08065 0.3071480434314712 0.5343834526297686 0.15846850393876033 id22674 0.03681934873324811 0.9406602107339027 0.022520440532849274 id25018 0.2405451111025488 0.

5.3 Download Spooky CSV

In [0]:

%fs ls /FileStore/tables/